## 6. 分子動力学シミュレーション

### まとめと演習

#### 1. Lennard-Jones流体のミクロカノニカル（ NVE 一定 ）シミュレーション

##### Lennard-Jones model

<img src="fig/LJ.png">

- 粒子対 $i,j$ 間のポテンシャルエネルギー関数
$$
\phi(r_{ij})=4\epsilon\left[\left(\frac{\sigma}{r_{ij}}\right)^{12}-\left(\frac{\sigma}{r_{ij}}\right)^{6}\right],\ \ \ \ r_{ij}=\left|{\bf r}_{i}-{\bf r}_{j}\right|
$$
 右辺第一項は近距離での粒子の反発を表し，第二項は 粒子間の引力を表す．Lennard-Jones model はアルゴンなど希ガスの性質を比較的よく再現し，与えられた熱力学状態（粒子数 $N$，温度 $T$，体積 $V=\rho N$）のもとで気体・液体・固体の３相（あるいはそれらの共存状態）をとることが出来る．

- 系全体のポテンシャルエネルギー
$$
E_p=\sum_{i=2}^{N}\sum_{j=1}^{i-1}\phi(r_{ij})
$$

- 系全体の運動エネルギー

$$E_k = \frac{1}{2}m\sum_{i=2}^{N}{\bf v}_i^2$$

- 粒子の運動方程式（Newton）

$$
\dfrac{d{\bf r}_i}{dt}={\bf v}_i
$$

$$
m\dfrac{d{\bf v}_i}{dt}=-\dfrac{\partial E_p}{\partial {\bf r}_i}
=-\sum_{j\ne i}^{N}w(r_{ij})\frac{{\bf r}_{ij}}{r_{ij}^2},
\ \ \ \ \ \ w(r_{ij})=r_{ij}\dfrac{d \phi(r_{ij})}{d r_{ij}}
$$

- Verocity Verlet method
$$
{\bf v}_{i}^* = {\bf v}_{i}(t) + \dfrac{{\bf f}_{i}(t)}{m} \frac{dt}{2}
$$

$$
{\bf r}_{i}(t+dt) = {\bf r}_{i}(t) + {\bf v}^*_i dt 
$$

$$
{\bf v}_{i}(t+dt) = {\bf v}_{i}^*(t) + \dfrac{{\bf f}_{i}(t+dt)}{m}\frac{dt}{2}
$$

##### Import library

In [1]:
%matplotlib inline
import numpy as np            
import matplotlib.pyplot as plt
import sys

##### Input/Output simulation parameters

In [2]:
N=108 #NUMBER OF PARTICLES
DENS=0.7 #DENSITY
NSTEP =15000 #NUMBER OF STEPS
NEQUIL=5000  #NUMBER OF STEPS FOR EQUILIBRATION
IPRINT=1000 #NUMBER OF STEPS BETWEEN OUTPUT LINES
RCUT=2.0 #POTENTIAL CUTOFF DISTANCE
RMIN=0.9 #CORE RADIUS TO AVOID OVERLAP
DT=0.005 # TIME INCREMENT
FREE=3.0 # System dimension
L = pow(N / DENS, 1.0 / 3.0) # pow(x,y) = x**y
if RCUT > 0.5*L:
    RCUT = 0.5*L
VX=np.zeros(N)
VY=np.zeros(N)
VZ=np.zeros(N)
FX=np.zeros(N)
FY=np.zeros(N)
FZ=np.zeros(N)
#write input parameter
print(" NUMBER OF PARTCLES                  =%10d"%N)
print(" NUMBER OF STEPS                     =%10d"%NSTEP)
print(" NUMBER OF STEPS FOR EQUILIBRATION   =%10d"%NEQUIL)
print(" OUTPUT FREQUENCY                    =%10d"%IPRINT)
print(" DENSITY                             =%10.4f"%DENS)
print(" POTENTIAL CUTOFF                    =%10.4f"%RCUT)

 NUMBER OF PARTCLES                  =       108
 NUMBER OF STEPS                     =     15000
 NUMBER OF STEPS FOR EQUILIBRATION   =      5000
 OUTPUT FREQUENCY                    =      1000
 DENSITY                             =    0.7000
 POTENTIAL CUTOFF                    =    2.0000


##### Define functions

- FORCE(pL, pRCUT,  RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
$$
{\bf f}_i=-\sum_{j\ne i}^{N}w(r_{ij})\frac{{\bf r}_{ij}}{r_{ij}^2}
$$

- KINET(VX, VY, VZ)
$$E_k = \frac{1}{2}m\sum_{i=2}^{N}{\bf v}_i^2$$

- MOVEA(pDT, pL, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)

 Verocity Verlet part A:
$$
{\bf v}_{i}^* = {\bf v}_{i}(t) + \dfrac{{\bf f}_{i}(t)}{m} \frac{dt}{2}
$$
$${\bf r}_{i}(t+dt) = {\bf r}_{i}(t) + {\bf v}^*_i dt 
$$


- MOVEB(pDT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)

 Verocity Verlet part B:
$$
{\bf v}_{i}(t+dt) = {\bf v}_{i}^*(t) + \dfrac{{\bf f}_{i}(t+dt)}{m}\frac{dt}{2}$$


In [3]:
def FORCE(pL, pRCUT,  RX, RY, RZ, VX, VY, VZ, FX, FY, FZ):
    RCUTSQ = pow(pRCUT / pL, 2.0)
    SIGSQ  = pow(pL, -2.0)
    for I in range(N):
        FX[I] = 0.0
        FY[I] = 0.0
        FZ[I] = 0.0
    
    pV = 0.0
    pW = 0.0
    NCUT = 0
#CONDUCT OUTER LOOP OVER ATOMS 
    for I in range(N-1):
        RXI = RX[I]
        RYI = RY[I]
        RZI = RZ[I]
        FXI = FX[I]
        FYI = FY[I]
        FZI = FZ[I]
#CONDUCT INNER LOOP OVER ATOMS
        for J in range(I+1,N):
            RXIJ = RXI - RX[J]
            RYIJ = RYI - RY[J]
            RZIJ = RZI - RZ[J]
#MINIMUM IMAGE THE PAIR SEPARATIONS
            RXIJ -= np.floor(RXIJ + 0.5)
            RYIJ -= np.floor(RYIJ + 0.5)
            RZIJ -= np.floor(RZIJ + 0.5)
            RIJSQ = RXIJ*RXIJ + RYIJ*RYIJ + RZIJ*RZIJ
            if RIJSQ < RCUTSQ :
                SR2   = SIGSQ / RIJSQ
                SR6   = SR2 * SR2 * SR2
                SR12  = SR6 * SR6
                VIJ   = 4.0 * (SR12 - SR6)
                WIJ   = 24.0 * (2.0 * SR12 - SR6)
                pV   += VIJ
                pW   += WIJ
                FIJ   = WIJ / RIJSQ
                FXIJ  = FIJ * RXIJ
                FYIJ  = FIJ * RYIJ
                FZIJ  = FIJ * RZIJ
                FXI   += FXIJ
                FYI   += FYIJ
                FZI   += FZIJ
                FX[J] -= FXIJ
                FY[J] -= FYIJ
                FZ[J] -= FZIJ
                NCUT += 1
#END OF INNER LOOP 
        FX[I] = FXI
        FY[I] = FYI
        FZ[I] = FZI
#END OF OUTER LOOP

#CONVERT FORCE INTO LJ UNIT 
    for I in range(N):
        FX[I] /= pL
        FY[I] /= pL
        FZ[I] /= pL
#CALCULATE POTENTIAL SHIFT  */
    SR2  = SIGSQ / RCUTSQ
    SR6  = SR2 * SR2 * SR2
    SR12 = SR6 * SR6
    VIJ  = 4.0 * (SR12 -SR6)
    pVC = pV - NCUT * VIJ
    return pV, pW, pVC ,FX ,FY ,FZ

def KINET(VX, VY, VZ):
#COMPUTES KINETIC ENERGY
    pK = 0.0
    for I in range(N):
        pK += VX[I]*VX[I]+VY[I]*VY[I]+VZ[I]*VZ[I]
    pK *= 0.5
    return pK

def MOVEA(pDT, pL, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ):
#/*  FIRST PART OF VELOCITY VERLET ALGORITHM  */
    DT2 = pDT / 2.0
    DTSQ2 = pDT * DT2
    for I in range(N):
        RX[I] += (pDT*VX[I] + DTSQ2*FX[I]) / pL
        RY[I] += (pDT*VY[I] + DTSQ2*FY[I]) / pL
        RZ[I] += (pDT*VZ[I] + DTSQ2*FZ[I]) / pL
        VX[I] += DT2 * FX[I]
        VY[I] += DT2 * FY[I]
        VZ[I] += DT2 * FZ[I]
    return FX, FY, FZ, VX, VY, VZ

def MOVEB(pDT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ):
#SECOND PART OF VELOCITY VERLET ALGORITHM 
    DT2 = pDT / 2.0
    pK = 0.0
    for I in range(N):
        VX[I] += DT2 * FX[I]
        VY[I] += DT2 * FY[I]
        VZ[I] += DT2 * FZ[I]
        pK += VX[I]*VX[I] + VY[I]*VY[I] + VZ[I]*VZ[I]
    pK *= 0.5
    return pK, VX, VY, VZ

##### Create random initial configuration

In [4]:
#RANDOM INITIAL CONFIGURATION 
RX = np.zeros(N)
RY = np.zeros(N)
RZ = np.zeros(N)
np.random.seed(0)
for I in range(N):
    OL=1
    while OL == 1:
        OL=0
        RX[I]=np.random.rand()-0.50
        RY[I]=np.random.rand()-0.50
        RZ[I]=np.random.rand()-0.50
        for J in range(I):
            sys.stdout.write("\rI =%8d"%I+"/ %8d"%N+",  J =%8d"%J)
            sys.stdout.flush()
            DX=RX[I]-RX[J]
            DY=RY[I]-RY[J]
            DZ=RZ[I]-RZ[J]
            DX -= np.floor(DX+0.50)
            DY -= np.floor(DY+0.50)
            DZ -= np.floor(DZ+0.50)
            DR=np.sqrt(DX*DX+DY*DY+DZ*DZ)
            if DR*L <= RMIN:
                OL=1
                break
#CALCULATE LONG-RANGE CORRECTIONS 
SR3 = pow(1.0 / RCUT, 3.0)
SR9 = SR3 * SR3 * SR3
VLRC12 =  8.0 * np.pi *DENS * N * SR9 / 9.0
VLRC6  = - 8.0 * np.pi *DENS * N * SR3 / 3.0
VLRC = VLRC12 + VLRC6
WLRC12 = 12.0 * VLRC12
WLRC6  =  6.0 * VLRC6
WLRC = WLRC12 + WLRC6

#CALCULATE INITIAL VALUES  
V, W ,VC ,FX ,FY ,FZ = FORCE(L, RCUT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
K = KINET(VX, VY, VZ)
KN = K / N
TEMP = 2.0 * KN / FREE
VS = (V + VLRC) / N
WS = (W + WLRC) / N
PS = DENS * TEMP + (W + WLRC) / (3.0 * L*L*L)
print("\n INITIAL V   =    %16.8e"%VS)
print(" INITIAL W   =    %16.8e"%WS)
print(" INITIAL P   =    %16.8e"%PS)

I =      56/      108,  J =      22

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =      81/      108,  J =      19

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =      92/      108,  J =      48

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =     100/      108,  J =       8

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =     106/      108,  J =      66

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



##### Main MD routine

In [5]:
import time
start = time.time()
#/*******************************************************************/
#/*  MAIN LOOP BEGINS                                               */
#/*******************************************************************/
print("**** START OF DYNAMICS ****\n")
print("    TIMESTEP     ENERGY    CUTENERGY    KINETIC    POTENTIAL    PRESSURE  TEMPERATURE")
for STEP in range(1,NSTEP+1):
    #ZERO ACCUMULATORS 
    if STEP == 1 or STEP == NEQUIL+1:
        ACV  = 0.0
        ACK  = 0.0
        ACE  = 0.0
        ACEC = 0.0
        ACP  = 0.0
        ACT  = 0.0
        ACVSQ  = 0.0
        ACKSQ  = 0.0
        ACESQ  = 0.0
        ACECSQ = 0.0
        ACPSQ  = 0.0
        ACTSQ  = 0.0
        FLV  = 0.0
        FLK  = 0.0
        FLE  = 0.0
        FLEC = 0.0
        FLP  = 0.0
        FLT  = 0.0
#/*  VELOCITY VERLET ALGORITHM         */
#/*  Update positions r(t) -> r(t+dt)  */
#/*  and Velocities v(t) -> v(t+dt/2)  */
    FX, FY, FZ, VX, VY, VZ = MOVEA(DT, L, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
#/*  Calculate force f(t+dt)  */
    V, W, VC, FX, FY, FZ  =FORCE(L, RCUT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
    #print("V = %f, W = %f" %(V,W))
#/*  Update velocities v(t+dt/2) -> v(t+dt) by using f(t+dt)  */
    K, VX, VY, VZ = MOVEB(DT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
#/*  INCLUDE LONG-RANGE CORRECTIONS  */
    V += VLRC
    W += WLRC
#/*  CALCULATE INSTANTANEOUS VALUES  */
    E    = K + V
    EC   = K + VC
    VN   = V  / N
    KN   = K  / N
    EN   = E  / N
    ECN  = EC / N
    TEMP = 2.0 * KN / FREE
    PRES = DENS * TEMP + W / (3.0 * L*L*L)
#/*  INCREMENT ACCUMULATORS  */
    ACE  += EN
    ACEC += ECN
    ACK  += KN
    ACV  += VN
    ACP  += PRES
    ACESQ  += EN * EN
    ACECSQ += ECN * ECN
    ACKSQ  += KN * KN
    ACVSQ  += VN * VN
    ACPSQ  += PRES * PRES
#/*  PERFORM PERIODIC OPERATIONS    */
#/*  WRITE OUT RUNTIME INFORMATION  */
    if STEP%IPRINT == 0:
        print("  %8d  %10.4f  %10.4f  %10.4f  %10.4f  %10.4f  %10.4f\n" %(STEP, EN, ECN, KN, VN, PRES, TEMP))
#        sys.stdout.write("\rSTEP =%8d"%STEP+"/ %8d"%NSTEP+",  E =%16.8f"%EN+",  T =%16.8e"%TEMP+",  P =%16.8e"%PRES)
#        sys.stdout.flush()
#/*******************************************************************/
#/*  MAIN LOOP ENDS                                                 */
#/*******************************************************************/
end = time.time()
print ("\n")
print ("elapsed_time:{0}".format(end - start) + "[sec]")

**** START OF DYNAMICS ****

    TIMESTEP     ENERGY    CUTENERGY    KINETIC    POTENTIAL    PRESSURE  TEMPERATURE
      1000     -2.5991     -1.1971      2.0971     -4.6962      0.9915      1.3980

      2000     -2.5888     -1.1971      2.1674     -4.7562      0.4201      1.4449

      3000     -2.5947     -1.1978      1.8833     -4.4780      1.8689      1.2556

      4000     -2.5999     -1.1974      1.9944     -4.5943      1.2030      1.3296



KeyboardInterrupt: 

##### Output average values

In [ ]:
print("**** END OF DYNAMICS ****")
#  OUTPUT RUN AVERAGES  
NORM = STEP - NEQUIL
AVE  = ACE  / NORM
AVEC = ACEC / NORM
AVK  = ACK  / NORM
AVV  = ACV  / NORM
AVP  = ACP  / NORM
ACESQ  = (ACESQ  / NORM) - AVE * AVE
ACECSQ = (ACECSQ / NORM) - AVEC* AVEC
ACKSQ  = (ACKSQ  / NORM) - AVK * AVK
ACVSQ  = (ACVSQ  / NORM) - AVV * AVV
ACPSQ  = (ACPSQ  / NORM) - AVP * AVP
if ACESQ  > 0.0:
    FLE  = np.sqrt(ACESQ)
if ACECSQ > 0.0:
    FLEC = np.sqrt(ACECSQ)
if ACKSQ  > 0.0:
    FLK  = np.sqrt(ACKSQ)
if ACVSQ  > 0.0:
    FLV  = np.sqrt(ACVSQ)
if ACPSQ  > 0.0:
    FLP  = np.sqrt(ACPSQ)
AVT = AVK * 2.0 / FREE
FLT = FLK * 2.0 / FREE

print("TEMPERATURE  = %10.4f"%TEMP)
print("DENSITY      = %10.4f"%DENS)
print("")
print("             ENERGY      CUTENERGY   KINETIC     POTENTIAL   PRESSURE    TEMPERATURE")
print("AVERAGES  %10.5f  %10.5f  %10.5f  %10.5f  %10.5f  %10.5f" %(AVE, AVEC, AVK, AVV, AVP, AVT))
print("FLUCTS    %10.5f  %10.5f  %10.5f  %10.5f  %10.5f  %10.5f" %(FLE, FLEC, FLK, FLV, FLP, FLT))

#### 2. Lennard-Jones流体のカノニカル（ NVT 一定 ）シミュレーション

##### Nose-Hoover方法

- 粒子の運動方程式（Nose-Hoover）

$$
\dfrac{d{\bf r}_i}{dt}={\bf v}_i
$$

$$
m\dfrac{d{\bf v}_i}{dt}=-\dfrac{\partial E_p}{\partial {\bf r}_i}-\zeta{\bf v}_i
%=-\sum_{j\ne i}^{N}w(r_{ij})\frac{{\bf r}_{ij}}{r_{ij}^2}-\zeta{\bf v}_i,
%\ \ \ \ \ \ w(r_{ij})=r_{ij}\dfrac{d \phi(r_{ij})}{d r_{ij}}
$$

$$
\dfrac{d \zeta}{dt}=\dfrac{1}{Q}\left[m\sum_{i=1}^N {\bf v}_i^2 -3 N k_B T\right]
$$

$$
\dfrac{1}{s}\dfrac{d s}{dt}=\zeta\ \ \ \ \ \rightarrow\ \ \ \ \ \dfrac{d \ln s}{dt}=\zeta
$$

- Verocity Verlet method: Part A

$$
{\bf v}_{i}^* = {\bf v}_{i}(t) + \left[\dfrac{{\bf f}_{i}(t)}{m} - \zeta(t){\bf v}_i(t)\right] \frac{dt}{2}
$$

$$
{\bf r}_{i}(t+dt) = {\bf r}_{i}(t) + {\bf v}_{i}^*dt 
$$

$$
\zeta^* = \zeta(t) + 
\left[m\sum_{i=1}^N {\bf v}_i(t)^2 -3 N T\right]
\frac{dt}{2Q}
$$

$$
\ln{s}(t+dt) = \ln{s}(t) + \zeta^*dt 
$$

- Verocity Verlet method: Part B

$$
{\bf v}_{i}(t+dt) = {\bf v}_{i}^* + 
\left[
\dfrac{{\bf f}_{i}(t+dt)}{m} - \zeta(t+dt){\bf v}_{i}(t+dt)
\right] \frac{dt}{2}
$$

$$
\zeta(t+dt) = \zeta^* + 
\left[m\sum_{i=1}^N {\bf v}_i^2(t+dt) -3 N T\right]
\frac{dt}{2Q}
$$

上式はどちらも右辺に $t+dt$ の項があるため陽解法では解けない．さらに非線形なので Newton-Raphson法（Newton法）で解く．

$$
{\bf H}=\left[{\bf h}_1({\bf v}_{i},\zeta),\cdots{\bf h}_i({\bf v}_{i},\zeta),\cdots{\bf h}_N({\bf v}_{i},\zeta),h_{3N+1}({\bf v}_{i},\zeta)\right]
=\left[{h}_1(x_1,\cdots x_{3N+1})\cdots h_{3N+1}(x_1,\cdots x_{3N+1})\right]
$$

$$
{\bf h}_{i}({\bf v}_{i},\zeta) = {\bf v}_{i}^* + \left[\dfrac{{\bf f}_{i}}{m} - \zeta {\bf v}_{i}\right]\frac{dt}{2} - {\bf v}_{i}=[0,0,0]
$$

$$
h_{3N+1}({\bf v}_{i},\zeta) = \zeta^* + \left[m\sum_{i=1}^{N}{\bf v}_i^2 - 3NT\right]\frac{dt}{2Q} -\zeta = 0
$$

で ${\bf H}$ を定義し，その各要素 
$
h_{i}
$
を一次の項までTaylor展開すると

$$
h_{i}(x_1+\delta x_1,\cdots x_j+\delta x_j,\cdots x_{3N+1}+\delta x_{3N+1})
 = h_{i}(x_1,\cdots x_j,\cdots x_{3N+1}) + \sum_{j=1}^{3N+1}\frac{\partial h_{i}}{\partial x_j}\delta x_j
$$

である．ここで
$$
h_{i}(x_1+\delta x_1,\cdots x_j+\delta x_j,\cdots x_{3N+1}+\delta x_{3N+1})=0
$$
となれば解が求まったことになるので

$$
-h_{i}(x_1,\cdots x_j,\cdots x_{3N+1}) = 
\sum_{j=1}^{3N+1}\frac{\partial h_{i}}{\partial x_j}\delta x_j
$$
を解く．最終的には

$$
\delta x_{3N+1} = \dfrac{-h_{3N+1}\left(\zeta\dfrac{\Delta t}{2} +1\right)-m\sum_{i=1}^{3N}h_{i} {x}_{i}\dfrac{\Delta t}{Q}}{\zeta\dfrac{\Delta t}{2} +1 - m\sum_{i=1}^{3N} {x}_{i}^2\dfrac{\Delta t^2}{2Q}}
$$

$$
\delta x_i = -\dfrac{\left(h_{i} + \delta x_{3N+1} x_{i}\dfrac{\Delta t}{2}\right)}{\zeta\dfrac{\Delta t}{2} +1}
$$


##### Import library

In [6]:
%matplotlib inline
import numpy as np            
import matplotlib.pyplot as plt
import sys

##### Input/Output simulation parameters

In [7]:
N=108 #NUMBER OF PARTICLES
DENS=0.7 #DENSITY
TEMPSET=1.0 #TEMPERATURE
NSTEP =15000 #NUMBER OF STEPS
NEQUIL=5000  #NUMBER OF STEPS FOR EQUILIBRATION
IPRINT=1000 #NUMBER OF STEPS BETWEEN OUTPUT LINES
RCUT=2.0 #POTENTIAL CUTOFF DISTANCE
RMIN=0.85 #CORE RADIUS TO AVOID OVERLAP
DT=0.005 # TIME INCREMENT
FREE=3.0 # System dimension
TMAX = 5000
T0MAX = 100
MM = 2147483647.0   # 2**31-1 for mrand() 
AA = 48828125       #5**11 for mrand()  
NN = 669895741      #for mrand()
LOGS = 0.0
ZETA = 0.0
G = 3.0 * N
L = pow(N / DENS, 1.0 / 3.0) # pow(x,y) = x**y
if RCUT > 0.5*L:
    RCUT = 0.5*L
    
#ENTER STEPS FOR CALCULATING TIME CORRELATIONS
NSAMP = 1
#ENTER Q
Q = 4
#  DATA POINTS FOR VELOCITY AUTO CORRELATION FUNCTION    
#  IS TAKEN EVERY NSAMP STEP, WHILE                      
#  INITIAL TIMES FOR VELOCITY AUTO CORRELATION FUNCTION  
#  IS TAKEN EVERY NSAMP*IT0 STEP                         
IT0 = 10
#  INITIALIZE NUMBER OF INITIAL TIMES T0 AND                
#  DATA POINTS FOR VELOCITY AUTO CORRELATION FUNCTION TVACF 
T0 = 0
TVACF = 0
    
VX=np.zeros(N)
VY=np.zeros(N)
VZ=np.zeros(N)
FX=np.zeros(N)
FY=np.zeros(N)
FZ=np.zeros(N)
#write input parameter
print(" NUMBER OF PARTCLES                  =%10d"%N)
print(" NUMBER OF STEPS                     =%10d"%NSTEP)
print(" NUMBER OF STEPS FOR EQUILIBRATION   =%10d"%NEQUIL)
print(" OUTPUT FREQUENCY                    =%10d"%IPRINT)
print(" DENSITY                             =%10.4f"%DENS)
print(" TEMPERATURE_SET                     =%10.4f"%TEMPSET)
print(" POTENTIAL CUTOFF                    =%10.4f"%RCUT)

 NUMBER OF PARTCLES                  =       108
 NUMBER OF STEPS                     =     15000
 NUMBER OF STEPS FOR EQUILIBRATION   =      5000
 OUTPUT FREQUENCY                    =      1000
 DENSITY                             =    0.7000
 TEMPERATURE_SET                     =    1.0000
 POTENTIAL CUTOFF                    =    2.0000


##### Define functions

In [8]:
def mrand(NN,AA,MM):
    NN *= AA
    ra = NN/MM
    if ra < 0 :
        ra += 1.0
    return ra

def FORCE(pL, pRCUT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ):
    RCUTSQ = pow(pRCUT / pL, 2.0)
    SIGSQ  = pow(pL, -2.0)
    for I in range(N):
        FX[I] = 0.0
        FY[I] = 0.0
        FZ[I] = 0.0    
    pV = 0.0
    pW = 0.0
    NCUT = 0
#CONDUCT OUTER LOOP OVER ATOMS 
    for I in range(N-1):
        RXI = RX[I]
        RYI = RY[I]
        RZI = RZ[I]
        FXI = FX[I]
        FYI = FY[I]
        FZI = FZ[I]
#CONDUCT INNER LOOP OVER ATOMS
        for J in range(I+1,N):
            RXIJ = RXI - RX[J]
            RYIJ = RYI - RY[J]
            RZIJ = RZI - RZ[J]
#MINIMUM IMAGE THE PAIR SEPARATIONS
            RXIJ -= np.floor(RXIJ + 0.5)
            RYIJ -= np.floor(RYIJ + 0.5)
            RZIJ -= np.floor(RZIJ + 0.5)
            RIJSQ = RXIJ*RXIJ + RYIJ*RYIJ + RZIJ*RZIJ
            if RIJSQ < RCUTSQ :
                SR2   = SIGSQ / RIJSQ
                SR6   = SR2 * SR2 * SR2
                SR12  = SR6 * SR6
                VIJ   = 4.0 * (SR12 - SR6)
                WIJ   = 24.0 * (2.0 * SR12 - SR6)
                pV   += VIJ
                pW   += WIJ
                FIJ   = WIJ / RIJSQ
                FXIJ  = FIJ * RXIJ
                FYIJ  = FIJ * RYIJ
                FZIJ  = FIJ * RZIJ
                FXI   += FXIJ
                FYI   += FYIJ
                FZI   += FZIJ
                FX[J] -= FXIJ
                FY[J] -= FYIJ
                FZ[J] -= FZIJ
                NCUT += 1
#END OF INNER LOOP 
        FX[I] = FXI
        FY[I] = FYI
        FZ[I] = FZI
#END OF OUTER LOOP

#CONVERT FORCE INTO LJ UNIT 
    for I in range(N):
        FX[I] /= pL
        FY[I] /= pL
        FZ[I] /= pL
#CALCULATE POTENTIAL SHIFT  */
    SR2  = SIGSQ / RCUTSQ
    SR6  = SR2 * SR2 * SR2
    SR12 = SR6 * SR6
    VIJ  = 4.0 * (SR12 -SR6)
    pVC = pV - NCUT * VIJ
    return pV, pW, pVC ,FX ,FY ,FZ

def KINET(VX, VY, VZ):
#COMPUTES KINETIC ENERGY
    pK = 0.0
    for I in range(N):
        pK += VX[I]*VX[I]+VY[I]*VY[I]+VZ[I]*VZ[I]
    pK *= 0.5
    return pK

#  FIRST PART OF VELOCITY VERLET ALGORITHM  

def MOVEA(pDT, pL, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ,LOGS, ZETA, Q, TEMPSET, G):

    DT2 = pDT / 2.0
    DTSQ2 = pDT * DT2
    K2 = 0.0
    for I in range(N):
        FXI = FX[I] - ZETA * VX[I]
        FYI = FY[I] - ZETA * VY[I]
        FZI = FZ[I] - ZETA * VZ[I]
        RX[I] += (pDT * VX[I] + DTSQ2 * FXI)/ pL
        RY[I] += (pDT * VY[I] + DTSQ2 * FYI)/ pL
        RZ[I] += (pDT * VZ[I] + DTSQ2 * FZI)/ pL
        K2 += VX[I]*VX[I] + VY[I]*VY[I] + VZ[I]*VZ[I]
        VX[I] += DT2 * FXI
        VY[I] += DT2 * FYI
        VZ[I] += DT2 * FZI

    FS = (K2-G*TEMPSET)/Q;
    LOGS += pDT*ZETA + DTSQ2*FS;
    ZETA += DT2*FS;
    
    return LOGS, ZETA, RX, RY, RZ, VX, VY, VZ

#  SECOND PART OF VELOCITY VERLET ALGORITHM WITH              
#  NEWTON RAPHSON ITERATIVE DETERMINATIONS OF NEW VELOCITIES

def MOVEB(pDT, pL, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ, LOGS, ZETA, Q, TEMPSET, G):
    
    DT2 = pDT/2.0
    ERR = 1.0E-8
    K2 = 0.0
    VXN = np.zeros(N)
    VYN = np.zeros(N)
    VZN = np.zeros(N)
    VXO = np.zeros(N)
    VYO = np.zeros(N)
    VZO = np.zeros(N)
    BX = np.zeros(N)
    BY = np.zeros(N)
    BZ = np.zeros(N)
    
    for I in range(N):
        VXN[I] = VX[I]
        VYN[I] = VY[I]
        VZN[I] = VZ[I]
        K2 += VXN[I]*VXN[I] + VYN[I]*VYN[I] + VZN[I]*VZN[I]
        
    ZETAN = ZETA
    READY = 0

#####################################################    
#  START OF THE NEWTON RAPHSON METHOD 
    for ITER in range(100):
        ZETAO = ZETAN
        DELZ = 0.0
        for I in range(N):
            VXO[I] = VXN[I]
            VYO[I] = VYN[I]
            VZO[I] = VZN[I]
            BX[I] = -DT2*(FX[I]-ZETAO*VXO[I]) - (VX[I]-VXO[I])
            RI = VXO[I]*pDT/Q
            DELZ += RI*BX[I]
            BY[I] = -DT2*(FY[I]-ZETAO*VYO[I]) - (VY[I]-VYO[I])
            RI = VYO[I]*pDT/Q
            DELZ += RI*BY[I]
            BZ[I] = -DT2*(FZ[I]-ZETAO*VZO[I]) - (VZ[I]-VZO[I])
            RI = VZO[I]*pDT/Q
            DELZ += RI*BZ[I]       
        DI = -(ZETAO*DT2+1)
        DELZ -= DI*((-K2+G*TEMPSET)*DT2/Q-(ZETA-ZETAO))
        DELZ /= (- pDT*DT2*K2/Q+DI)
        K2 = 0.0
        
#  ITERATIVE DETERMINATIONS OF CORRECT VELOCITIES AT t+dt  
        for I in range(N):
            VXN[I] += (BX[I]+DT2*VXO[I]*DELZ)/DI
            VYN[I] += (BY[I]+DT2*VYO[I]*DELZ)/DI
            VZN[I] += (BZ[I]+DT2*VZO[I]*DELZ)/DI
            K2 += VXN[I]*VXN[I] + VYN[I]*VYN[I] + VZN[I]*VZN[I]
        ZETAN = ZETAO + DELZ
        
#  TEST FOR CONVERGENCE  
        READY = 1
        if abs((ZETAN-ZETAO)/ZETAN)>ERR:
            break
        for I in range(N):
            if abs((VXN[I]-VXO[I])/VXN[I])>ERR:
                READY = 0
            if abs((VYN[I]-VYO[I])/VYN[I])>ERR:
                READY = 0
            if abs((VZN[I]-VZO[I])/VZN[I])>ERR:
                READY = 0
            if ready == 0:
                break
        if ready == 1:
            break

#  END OF THE NEWTON RAPHSON METHOD  
#####################################################

    for I in range(N):
        VX[I] = VXN[I]
        VY[I] = VYN[I]
        VZ[I] = VZN[I]
    
    ZETA = ZETAN
    pK = K2/2.0

    return pK, ZETA, VX, VY, VZ

##### Create random initial configuration

In [9]:
#RANDOM INITIAL CONFIGURATION 
RX = np.zeros(N)
RY = np.zeros(N)
RZ = np.zeros(N)
np.random.seed(0)
for I in range(N):
    OL=1
    while OL == 1:
        OL=0
        RX[I]=np.random.rand()-0.50
        RY[I]=np.random.rand()-0.50
        RZ[I]=np.random.rand()-0.50
        for J in range(I):
            sys.stdout.write("\rI =%8d"%I+"/ %8d"%N+",  J =%8d"%J)
            sys.stdout.flush()
            DX=RX[I]-RX[J]
            DY=RY[I]-RY[J]
            DZ=RZ[I]-RZ[J]
            DX -= np.floor(DX+0.50)
            DY -= np.floor(DY+0.50)
            DZ -= np.floor(DZ+0.50)
            DR=np.sqrt(DX*DX+DY*DY+DZ*DZ)
            if DR*L <= RMIN:
                OL=1
                break
#CALCULATE LONG-RANGE CORRECTIONS 
SR3 = pow(1.0 / RCUT, 3.0)
SR9 = pow(SR3, 3.0)
VLRC12 =  8.0 * np.pi * DENS * N * SR9 / 9.0
VLRC6  = -8.0 * np.pi * DENS * N * SR3 / 3.0
VLRC = VLRC12 + VLRC6
WLRC12 = 12.0 * VLRC12
WLRC6  =  6.0 * VLRC6
WLRC = WLRC12 + WLRC6
#CALCULATE INITIAL VALUES  
V, W ,VC ,FX ,FY ,FZ = FORCE(L, RCUT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
K = KINET(VX, VY, VZ)
KN = K / N
TEMP = 2.0 * KN / FREE
VS = (V + VLRC) / N
WS = (W + WLRC) / N
PS = DENS * TEMP + (W + WLRC) / (3.0 * L*L*L)
print("\n INITIAL V   =    %16.8e"%VS)
print(" INITIAL W   =    %16.8e"%WS)
print(" INITIAL P   =    %16.8e"%PS)
VXT0 = np.zeros(N*T0MAX).reshape(N,T0MAX)
VYT0 = np.zeros(N*T0MAX).reshape(N,T0MAX)
VZT0 = np.zeros(N*T0MAX).reshape(N,T0MAX)
VACF = np.zeros(TMAX)
RX0 = np.zeros(N*T0MAX).reshape(N,T0MAX)
RY0 = np.zeros(N*T0MAX).reshape(N,T0MAX)
RZ0 = np.zeros(N*T0MAX).reshape(N,T0MAX)
R2T = np.zeros(TMAX)
NVACF = np.zeros(TMAX)
TTV0 = np.zeros(T0MAX)

I =      59/      108,  J =      14

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =      86/      108,  J =      16

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =     101/      108,  J =       8

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



##### Main MD routine

In [10]:
import time
start = time.time()
#####################################################
#  MAIN LOOP BEGINS                                               
#####################################################
print("**** START OF DYNAMICS ****");
print("    TIMESTEP     H_NOSE       H_0       KINETIC    POTENTIAl    PRESSURE  TEMPERATURE")
for STEP in range(1,NSTEP+1):
    if STEP == 1 or STEP == NEQUIL+1:
#  ZERO ACCUMULATORS  
        ACV  = 0.0
        ACK  = 0.0
        ACE  = 0.0
        ACEC = 0.0
        ACP  = 0.0
        ACT  = 0.0
        ACVSQ  = 0.0
        ACKSQ  = 0.0
        ACESQ  = 0.0
        ACECSQ = 0.0
        ACPSQ  = 0.0
        ACTSQ  = 0.0
        FLV  = 0.0
        FLK  = 0.0
        FLE  = 0.0
        FLEC = 0.0
        FLP  = 0.0
        FLT  = 0.0
        T0 = 0
        TVACF = 0
        for I in range(TMAX):
            R2T[I] = 0
            NVACF[I] = 0
            VACF[I] = 0

#  VELOCITY VERLET ALGORITHM         
#  Update positions r(t) -> r(t+dt)  
#  and Velocities v(t) -> v(t+dt/2)  
    LOGS, ZETA, RX, RY, RZ, VX, VY, VZ = MOVEA(DT, L, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ,LOGS, ZETA, Q, TEMPSET, G)
#  Calculate force f(t+dt)  
    V, W, VC ,FX ,FY ,FZ = FORCE(L, RCUT, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ)
# Update velocities v(t+dt/2) -> v(t+dt) by using f(t+dt)  
    K, ZETA, VX, VY, VZ = MOVEB(DT, L, RX, RY, RZ, VX, VY, VZ, FX, FY, FZ, LOGS, ZETA, Q, TEMPSET, G)
#  INCLUDE LONG-RANGE CORRECTIONS  
    V += VLRC
    W += WLRC
#  CALCULATE INSTANTANEOUS VALUES  
    E    = K + VC + (ZETA*ZETA * Q)/2.0 + G*TEMPSET*LOGS
    EC   = K + V
    VN   = V  / N
    KN   = K  / N
    EN   = E  / N
    ECN  = EC / N
    TEMP = 2.0 * KN / FREE
    PRES = DENS * TEMP + W/(3.0 * L*L*L)
#  INCREMENT ACCUMULATORS  
    ACE  += EN
    ACEC += ECN
    ACK  += KN
    ACV  += VN
    ACP  += PRES
    ACESQ  += EN * EN
    ACECSQ += ECN * ECN
    ACKSQ  += KN * KN
    ACVSQ  += VN * VN
    ACPSQ  += PRES * PRES
#  PERFORM PERIODIC OPERATIONS    
#  WRITE OUT RUNTIME INFORMATION  
    if STEP%IPRINT == 0:
        print("  %8d  %10.4f  %10.4f  %10.4f  %10.4f  %10.4f  %10.4f" %(STEP, EN, ECN, KN, VN, PRES, TEMP))  
#        sys.stdout.write("\rSTEP =%8d"%STEP+"/ %8d"%NSTEP+",  E =%16.8f"%EN+",  T =%16.8e"%TEMP+",  P =%16.8e"%PRES)
#        sys.stdout.flush()

#  CALCULATE VELOCITY AUTO CORRELATION FUNCTION  
#  AND MEAN SQUARE DISPLACEMENT  
    if STEP%NSAMP == 0:
        TVACF += 1
#  SAMPLE VELOCITY AUTO CORRELATION FUNCTION AND  
#  MEAN SQUARE DISPLACEMENT                       
        if TVACF%IT0 == 0:
#  SAVE DATA WHICH WILL BE USED FOR CALCULATING VAF  
            TTEL = T0%T0MAX
            TTV0[TTEL] = TVACF
            for I in range(N):
                RX0[I][TTEL] = RX[I]
                RY0[I][TTEL] = RY[I]
                RZ0[I][TTEL] = RZ[I]
                VXT0[I][TTEL] = VX[I]
                VYT0[I][TTEL] = VY[I]
                VZT0[I][TTEL] = VZ[I]
            T0 += 1
                    
        for T in range(min(T0,T0MAX)):
#  CALCULATE CORRELATIONS BETWEEN DATA AT A PRESENT TIME AND  
#  THOSE AT PAST TIMES SAVED AS **0(T)                        
#  IDT PRESENTS THE TIME DIFFERENCE BETWEEN THEM              
            IDT = TVACF - TTV0[T]
            if IDT<TMAX :
                NVACF[int(IDT)] = 1
                for I in range(N):
                    VACF[int(IDT)] += VX[I]*VXT0[I][T] + VY[I]*VYT0[I][T] + VZ[I]*VZT0[I][T];
                    R2T[int(IDT)] += ((RX[I]-RX0[I][T])*(RX[I]-RX0[I][T]) + (RY[I]-RY0[I][T])*(RY[I]-RY0[I][T])+ (RZ[I]-RZ0[I][T])*(RZ[I]-RZ0[I][T])) * L*L     
#####################################################
#  MAIN LOOP ENDS                                           
#####################################################
end = time.time()
print ("\n")
print ("elapsed_time:{0}".format(end - start) + "[sec]")

**** START OF DYNAMICS ****
    TIMESTEP     H_NOSE       H_0       KINETIC    POTENTIAl    PRESSURE  TEMPERATURE


KeyboardInterrupt: 

In [ ]:
print("**** END OF DYNAMICS ****")
#  OUTPUT RUN AVERAGES  
NORM = (NSTEP - NEQUIL)
AVE  = ACE  / NORM
AVEC = ACEC / NORM
AVK  = ACK  / NORM
AVV  = ACV  / NORM
AVP  = ACP  / NORM
ACESQ  = (ACESQ  / NORM) - AVE  * AVE
ACECSQ = (ACECSQ / NORM) - AVEC * AVEC
ACKSQ  = (ACKSQ  / NORM) - AVK  * AVK
ACVSQ  = (ACVSQ  / NORM) - AVV  * AVV
ACPSQ  = (ACPSQ  / NORM) - AVP  * AVP
if ACESQ  > 0.0:
    FLE  = np.sqrt(ACESQ)
if ACECSQ > 0.0:
    FLEC = np.sqrt(ACECSQ)
if ACKSQ  > 0.0:
    FLK  = np.sqrt(ACKSQ)
if ACVSQ  > 0.0:
    FLV  = np.sqrt(ACVSQ)
if ACPSQ  > 0.0:
    FLP  = np.sqrt(ACPSQ)
AVT = AVK * 2.0 / FREE
FLT = FLK * 2.0 / FREE
print("TEMPERATURE  = %10.4f"%TEMP)
print("DENSITY      = %10.4f"%DENS)
print("")
print("             H_NOSE      H_0         KINETIC     POTENTIAl   PRESSURE    TEMPERATURE")
print("AVERAGES  %10.5f  %10.5f  %10.5f  %10.5f  %10.5f  %10.5f" %(AVE, AVEC, AVK, AVV, AVP, AVT))
print("FLUCTS    %10.5f  %10.5f  %10.5f  %10.5f  %10.5f  %10.5f" %(FLE, FLEC, FLK, FLV, FLP, FLT))

## 課題

### 1.
- NVE一定の分子動力学シミュレーションのサンプルプログラムをよく読み，内容を理解せよ．

### 2.
- Nose-Hoover運動方程式によるNVT一定の分子動力学シミュレーションのサンプルプログラムをよく読み，内容を理解せよ．

### 3.
- 前章のモンテカルロシミュレーションの課題と同様に，温度（単位：$\epsilon$）を４種類（$T=0.5, 1.0, 2.0, 4.0$），密度（単位：数$/\sigma^3$）を５種類（$\rho=0.1, 0.2, 0.4, 0.6, 0.8, 1.0$）の全組み合わせ（合計２０組）の状態についてNVT一定の分子動力学シミュレーションを行い，圧力のカノニカル平均値を求め，密度－圧力の等温線４本をグラフ化せよ．

### 4. （アドバンストな自習問題）
- シミュレーション実行中に，速度自己相関関数 VAC(t) 、平均２乗変位 R2T(t) のデータが計算されている．平均２乗変位を両対数のグラフにプロットし，Einstein則（ R2T(t)=6Dt）が成立していることを確認せよ．また，R2T(t) の短時間と長時間における時間依存性を調べ，その物理的な意味を考察せよ．

### 5. （アドバンストな自習問題）
- モンテカルロシミュレーションと違い，分子動力学シミュレーションでは輸送係数も計算できる．久保公式にしたがって速度自己相関関数の時間積分から粒子の自己拡散係数を求め，その密度依存性，温度依存性を議論せよ．
  